
# 🌼 RAG기법의 이해와 적용(1) - 2차시(24.11.29)

---

In [ ]:
pip install langchain_community

In [1]:
from langchain_community.document_loaders import RecursiveUrlLoader

DOCS_PAGE='https://sesac.seoul.kr/common/menu/html/900006001001/detail.do'

In [2]:
loader = RecursiveUrlLoader(DOCS_PAGE)

In [3]:
docs = loader.load()

In [4]:
print(f'연결된 페이지 {len(docs)}')

연결된 페이지 1


In [5]:
print(docs[0].page_content)

<!doctype html>
<!--[if IE 8]><html lang="ko" class="ie8"><![endif]-->
	<html lang="ko">
	<!--<![endif]-->
<head>
<meta charset="utf-8">
<meta http-equiv="X-UA-Compatible" content="IE=edge" />
<meta name="viewport" content="width=device-width,initial-scale=1.0,maximum-scale=1.0,minimum-scale=1.0,user-scalable=no" />
<meta name="format-detection" content="telephone=no, address=no, email=no" />
<title>청년취업사관학교</title>
<meta http-equiv="Content-type" content="text/html; charset=utf-8" />
<meta http-equiv="Cache-control" content="no-cache" />
<meta http-equiv="Pragma" content="no-cache" />
<meta http-equiv="Expires" content="0"/>
<meta http-equiv="X-UA-Compatible" content="IE=edge, chrome=1" />
<meta name="viewport" content="width=device-width,initial-scale=1.0,maximum-scale=1.0,minimum-scale=1.0,user-scalable=no" />
<meta name="format-detection" content="telephone=no, address=no, email=no" />
<!-- Global site tag (gtag.js) - Google Analytics -->
<script async src="https://www.googletagman

In [ ]:
import torch
from sentence_transformers import SentenceTransformer
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

In [8]:
model_name = "jhgan/ko-sbert-nli"

In [ ]:
encoder = SentenceTransformer(model_name, device=device)

In [11]:
embedding_dim = encoder.get_sentence_embedding_dimension()
print(f'문장을 임베딩 했을 때 생성되는 벡터 차원의 크기: {embedding_dim}')

문장을 임베딩 했을 때 생성되는 벡터 차원의 크기: 768


In [13]:
max_seq_length = encoder.get_max_seq_length()
print(f'모델이 처리할 수 있는 입력 문장의 최대 토큰 길이: {max_seq_length}')

모델이 처리할 수 있는 입력 문장의 최대 토큰 길이: 128


In [14]:
from langchain.text_splitter import RecursiveCharacterTextSplitter
import numpy as np

In [21]:
chunk_size = 224  # max_seq_length보다 조금 많이 줘도 괜찮다
chunk_overlap = np.round(chunk_size * 0.1, 0)
print(f'chunk_size: {chunk_size}, chunk_overlap: {chunk_overlap}')

chunk_size: 224, chunk_overlap: 22.0


In [22]:
child_splitter = RecursiveCharacterTextSplitter(
    chunk_size = chunk_size,
    chunk_overlap = chunk_overlap
)

In [23]:
chunks = child_splitter.split_documents(docs)

In [24]:
print(f'{len(docs)}개의 docs가 {len(chunks)}개의 문자로 나뉘었습니다.')
# chunk_size를 작은 값(문장 최대 토큰 길이이긴 하지만..)으로 주어서 많은 문자가 생김

1개의 docs가 225개의 문자로 나뉘었습니다.


In [26]:
string_list = []
for doc in chunks:
    if hasattr(doc, 'page_content'):
        string_list.append(doc.page_content)

In [27]:
embeddings = torch.tensor(encoder.encode(string_list))  # 인코딩 & tensor화

In [28]:
embeddings

tensor([[-0.2150, -0.1585,  0.2872,  ...,  0.3783, -0.4457,  0.9404],
        [-0.1551,  0.1841,  0.4740,  ...,  0.2883, -0.6413,  0.6247],
        [-0.6012, -0.9877,  0.4483,  ...,  0.7214,  0.0414,  0.5311],
        ...,
        [ 0.4452,  0.0573, -0.0778,  ...,  0.3551,  0.5948,  0.1823],
        [-0.2607, -0.4835,  0.3097,  ...,  0.1553, -0.8433,  0.0130],
        [ 0.5891, -0.1584,  0.5535,  ...,  0.1319, -1.0484,  0.0736]])

In [29]:
embeddings = np.array(embeddings/np.linalg.norm(embeddings))  # 정규화: 상대적인 값은 유지하면서 크기 조정

In [30]:
embeddings

array([[-7.7935302e-04, -5.7477504e-04,  1.0412072e-03, ...,
         1.3715390e-03, -1.6161108e-03,  3.4093696e-03],
       [-5.6221866e-04,  6.6763110e-04,  1.7186587e-03, ...,
         1.0454452e-03, -2.3250589e-03,  2.2647684e-03],
       [-2.1796632e-03, -3.5809735e-03,  1.6254772e-03, ...,
         2.6154511e-03,  1.5023381e-04,  1.9255261e-03],
       ...,
       [ 1.6142769e-03,  2.0790689e-04, -2.8202820e-04, ...,
         1.2875610e-03,  2.1566134e-03,  6.6087488e-04],
       [-9.4531145e-04, -1.7529303e-03,  1.1227516e-03, ...,
         5.6313613e-04, -3.0576054e-03,  4.7206559e-05],
       [ 2.1358989e-03, -5.7431596e-04,  2.0068383e-03, ...,
         4.7816648e-04, -3.8012527e-03,  2.6686123e-04]], dtype=float32)

In [31]:
converted_values = list(map(np.float32, embeddings))

In [32]:
converted_values  # tensor 형태를 모델의 input으로 넣기 위해 numpy 형태로 변경

[array([-7.7935302e-04, -5.7477504e-04,  1.0412072e-03,  3.1292678e-03,
        -4.0551955e-03, -2.0098747e-03, -3.9752928e-04, -6.5623096e-04,
        -3.8976604e-04, -1.0363894e-03,  2.4725862e-03,  1.8547359e-03,
        -3.7488888e-03, -6.6305284e-04, -3.0869601e-04,  1.0306614e-03,
        -1.5922665e-03, -2.3561511e-03, -4.5445595e-05, -4.5835605e-04,
         8.6026295e-04,  1.3591149e-03,  9.1633800e-04, -5.6244824e-03,
         2.0792522e-03,  1.6054950e-03,  2.9003937e-03,  4.6897217e-04,
         5.2493979e-04,  4.2783790e-03, -7.6603744e-04,  3.7651830e-03,
         1.1647609e-03, -5.4655486e-04,  3.1280082e-03, -2.0733110e-03,
        -7.8514119e-04,  3.5560399e-04, -2.7337091e-03, -5.1557473e-03,
         3.1444498e-03,  4.6109646e-03, -1.0862657e-04, -2.6895327e-04,
        -7.3297654e-04,  1.8641156e-05,  8.1502023e-04,  2.2751128e-03,
        -1.0476413e-03, -2.7994954e-03,  6.7483447e-04, -9.9269510e-04,
        -3.7896619e-04, -1.4191139e-03,  6.4785331e-03,  1.55562

In [33]:
dict_list = []
for chunk, vector in zip(chunks, converted_values):  # 잘게 자른 문장, 임베딩 된 벡터를 리스트 넘파이 배열로 바꿔준 것
    chunk_dict = {
        'chunk': chunk.page_content,
        'source': chunk.metadata.get('source', ''),  # source가 없으면 공백
        'vector': vector
    }
    dict_list.append(chunk_dict)  # 딕셔너리 형태로 바꿔서 다시 리스트에 넣기

In [34]:
dict_list

[{'chunk': '<!doctype html>\n<!--[if IE 8]><html lang="ko" class="ie8"><![endif]-->\n\t<html lang="ko">\n\t<!--<![endif]-->\n<head>\n<meta charset="utf-8">\n<meta http-equiv="X-UA-Compatible" content="IE=edge" />',
  'source': 'https://sesac.seoul.kr/common/menu/html/900006001001/detail.do',
  'vector': array([-7.7935302e-04, -5.7477504e-04,  1.0412072e-03,  3.1292678e-03,
         -4.0551955e-03, -2.0098747e-03, -3.9752928e-04, -6.5623096e-04,
         -3.8976604e-04, -1.0363894e-03,  2.4725862e-03,  1.8547359e-03,
         -3.7488888e-03, -6.6305284e-04, -3.0869601e-04,  1.0306614e-03,
         -1.5922665e-03, -2.3561511e-03, -4.5445595e-05, -4.5835605e-04,
          8.6026295e-04,  1.3591149e-03,  9.1633800e-04, -5.6244824e-03,
          2.0792522e-03,  1.6054950e-03,  2.9003937e-03,  4.6897217e-04,
          5.2493979e-04,  4.2783790e-03, -7.6603744e-04,  3.7651830e-03,
          1.1647609e-03, -5.4655486e-04,  3.1280082e-03, -2.0733110e-03,
         -7.8514119e-04,  3.5560399e-04,

In [ ]:
pip install pymilvus

In [36]:
from pymilvus import MilvusClient
import time

In [37]:
mc = MilvusClient(uri = 'milvus_test.db')

DEBUG:pymilvus.milvus_client.milvus_client:Created new connection using: fd41ffd676e14c7994e1aeb34a5b5191


In [39]:
collection_name = 'milvus_db'
if mc.has_collection(collection_name = collection_name):
    mc.drop_collection(collection_name = collection_name)

mc.create_collection(collection_name,
                    embedding_dim,
                    consistency_level='Eventually',
                    auto_id=True,
                    overwrite=True)

DEBUG:pymilvus.milvus_client.milvus_client:Successfully created collection: milvus_db
DEBUG:pymilvus.milvus_client.milvus_client:Successfully created an index on collection: milvus_db


In [40]:
print('데이터 삽입 시작!')
start_time = time.time()

mc.insert(collection_name, data=dict_list, progress_bar=True)

end_time = time.time()
print(f'삽입된 데이터 개수: {len(dict_list)}, 데이터 삽입에 걸리는 시간: {end_time-start_time:.2f}')

데이터 삽입 시작!
삽입된 데이터 개수: 225, 데이터 삽입에 걸리는 시간: 0.24


In [41]:
import torch.nn.functional as F

In [42]:
sample = '새싹이 뭐야?'

In [43]:
query_embeddings = torch.tensor(encoder.encode([sample]))

In [45]:
query_embeddings = F.normalize(query_embeddings, p=2, dim=1)  # 차원을 행 기준으로 정규화 (dim=1, 문장 하나? 그럼 질문이 다섯개이면 dim=5?)

In [46]:
query_embeddings = list(map(np.float32, query_embeddings))

In [48]:
output = list(dict_list[0].keys())

In [50]:
output.remove('vector')
output

['chunk', 'source']

In [51]:
top_k = 2

In [52]:
results = mc.search(
    collection_name, data=query_embeddings, output_fields=output,
    limit=top_k, consistency_level='Eventually'
)

In [53]:
results[0][0]['entity']['chunk']

'<!-- \tsesac -->\n\t<meta name="title"  content="꿈꾸는 개발자 데뷔코스, 새싹" />\n\t<meta name="description"  content="‘새싹’은 싹을 틔우기 위해 더 높은 곳을 향해 도전하고 한 단계 성장하여 기업과의 연결, 새로움을 추구하는 인재들의 공간입니다." />'

In [54]:
results[0][1]['entity']['chunk']

'<span class="ord">3</span>\r\n\t\t\t\t\t\t\t\t\t새싹은 기본역량뿐만 아니라 특화/응용역량까지 충분히 경험할 수 있습니다\r\n\t\t\t\t\t\t\t\t</div>\r\n\t\t\t\t\t\t\t\t<div class="desc">'

In [55]:
contexts = []
sources = []

contexts.append(results[0][0]['entity']['chunk'])
sources.append(results[0][0]['entity']['source'])

In [56]:
contexts

['<!-- \tsesac -->\n\t<meta name="title"  content="꿈꾸는 개발자 데뷔코스, 새싹" />\n\t<meta name="description"  content="‘새싹’은 싹을 틔우기 위해 더 높은 곳을 향해 도전하고 한 단계 성장하여 기업과의 연결, 새로움을 추구하는 인재들의 공간입니다." />']

In [ ]:
from openai import OpenAI
import os

api_key = input('API KEY')

In [58]:
os.environ['OPENAI_API_KEY'] = api_key
client = OpenAI()

In [59]:
system_prompt = f"""한국어로 되어있는 이 context를 이용해서 sample에 답하고,
                단어를 자연스럽게 풀어서 말해줘.

                context: {contexts}"""

In [60]:
system_prompt

'한국어로 되어있는 이 context를 이용해서 sample에 답하고,\n                단어를 자연스럽게 풀어서 말해줘.\n\n                context: [\'<!-- \\tsesac -->\\n\\t<meta name="title"  content="꿈꾸는 개발자 데뷔코스, 새싹" />\\n\\t<meta name="description"  content="‘새싹’은 싹을 틔우기 위해 더 높은 곳을 향해 도전하고 한 단계 성장하여 기업과의 연결, 새로움을 추구하는 인재들의 공간입니다." />\']'

In [61]:
llm = client.chat.completions.create(
    model='gpt-4o-mini',
    messages=[
        {'role': 'system', 'content': system_prompt},
        {'role': 'user', 'content': sample}
    ],
    temperature = 0.2,
    top_p = 0.95
)

In [62]:
generated_text = llm.choices[0].message.content
print(f'질문: {sample}')
print(f'생성된 답변: {generated_text}')

질문: 새싹이 뭐야?
생성된 답변: '새싹'은 꿈꾸는 개발자들이 데뷔할 수 있도록 돕는 프로그램이나 공간을 의미해요. 이곳은 사람들이 더 높은 목표를 향해 도전하고, 성장할 수 있도록 지원하는 곳입니다. 즉, 새로운 인재들이 기업과 연결되고, 새로운 경험을 쌓을 수 있는 기회를 제공하는 곳이라고 할 수 있어요.


In [65]:
print(llm.choices)

[Choice(finish_reason='stop', index=0, logprobs=None, message=ChatCompletionMessage(content="'새싹'은 꿈꾸는 개발자들이 데뷔할 수 있도록 돕는 프로그램이나 공간을 의미해요. 이곳은 사람들이 더 높은 목표를 향해 도전하고, 성장할 수 있도록 지원하는 곳입니다. 즉, 새로운 인재들이 기업과 연결되고, 새로운 경험을 쌓을 수 있는 기회를 제공하는 곳이라고 할 수 있어요.", refusal=None, role='assistant', audio=None, function_call=None, tool_calls=None))]
